In [1]:
%config Completer.use_jedi = False
import folium
from folium import GeoJson
import json
import pandas as pd
import geopandas as gpd

In [2]:
###################################
# loading basic geostatistical area (AGEB) geopandas
###################################

In [3]:
agebs = gpd.read_file('ageb_cdmx_epsg4326.geojson')

In [4]:
agebs['CVE_MUN']=agebs['CVE_MUN'].astype(int)
agebs['CVE_LOC']=agebs['CVE_LOC'].astype(int)

In [5]:
agebs['CVE_MUN']=agebs['CVE_MUN'].astype(str)
agebs['CVE_LOC']=agebs['CVE_LOC'].astype(str)

In [6]:
#agebs.head()

In [7]:
agebs['ID'] = agebs['CVE_MUN']+agebs['CVE_LOC']+agebs['CVE_AGEB']

In [8]:
#agebs.head()

In [9]:
# get AGEB cetroids
agebs['centroid'] = agebs.geometry.centroid

<ipython-input-9-ad32c0aee872>:2: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  agebs['centroid'] = agebs.geometry.centroid


In [10]:
#agebs.head()

In [11]:
agebs.drop(columns=['CVE_ENT','CVE_MUN','CVE_LOC', 'CVE_AGEB'], inplace=True)

In [12]:
agebs.set_index('ID',drop=True, inplace=True)

In [13]:
#agebs.head()

In [14]:
agebs.to_csv('geoms_agebs.csv')

In [15]:
###################################
# loading censo
###################################

In [16]:
censo = pd.read_pickle('censo.pkl')

In [17]:
#censo.head()

In [18]:
censo['ID'] = censo['MUN']+censo['LOC']+censo['AGEB']

In [19]:
censo.set_index('ID', drop=True, inplace=True)

In [20]:
#censo.head(2)

In [21]:
censo.drop(columns=['ENTIDAD','MUN','LOC', 'AGEB'], inplace=True)

In [22]:
censo['POBTOT']=censo.POBTOT.astype(str)

In [23]:
###################################
# merging data sets
###################################

In [24]:
agebs = pd.read_csv('geoms_agebs.csv', index_col='ID')

In [25]:
cdmx_data = agebs.join(censo)

In [26]:
cdmx_data.head()

geometry  \
ID                                                          
311783  MULTIPOLYGON (((-99.17286695004587 19.30630287...   
210148  MULTIPOLYGON (((-99.20697543022209 19.50085789...   
210190  MULTIPOLYGON (((-99.18981825992979 19.49955423...   
210932  MULTIPOLYGON (((-99.19067453964757 19.51041004...   
210237  MULTIPOLYGON (((-99.2082508899217 19.493856289...   

                                            centroid POBTOT POBFEM POBMAS  \
ID                                                                          
311783  POINT (-99.17517805774423 19.30467768139042)   3170   1714   1456   
210148  POINT (-99.20999103230413 19.49800417483361)   2513   1282   1231   
210190  POINT (-99.19254638757727 19.49463411433303)   8920   4720   4200   
210932  POINT (-99.18367767592652 19.50615608780749)    408    212    196   
210237   POINT (-99.21180432269377 19.4913352530251)   7093   3727   3366   

       GRAPROES GRAPROES_F GRAPROES_M POCUPADA POCUPADA_F POCUPADA_M PDESOCUP  \
ID                                                                              
311783    14.88      14.55      15.28     1856        937        919       62   
210148    13.26      12.92      13.63     1270        572        698       39   
210190    11.55      11.33       11.8     4975       2330       2645      134   
210932    11.74      11.79      11.69      214        104        110        *   
210237    11.13      11.03      11.24     3847       1763       2084      115   

       PDESOCUP_F PDESOCUP_M VIVPAR_HAB PRO_OCUP_C  
ID                                                  
311783         25         37       1132        0.6  
210148         13         26        739       0.62  
210190         54         80       2649       0.84  
210932          *          *        121       0.72  
210237         42         73       2042       0.88

In [ ]:
# Save to json

In [28]:
cdmx_data.to_json('mi_cdmx_data.json')

print(agebs['features'][0])

In [29]:
location=[19.436677, -99.143422]
zoom_start=11

agebs.keys()

agebs['features'][0]['properties']

In [32]:
# simple map load
m = folium.Map(location=location, zoom_start=zoom_start)
folium.GeoJson('./mi_cdmx_data-Copy1.geojson',).add_to(m)

folium.GeoJson(
    './mi_cdmx_data-Copy1.geojson',
    style_function=lambda feature: {
        "fillColor": "#ffff00",
        "color": "black",
        "weight": 2,
        "dashArray": "5, 5",
    },
).add_to(m)

In [33]:
m